In [2]:
import urllib.request
import zipfile
import os
import ssl


import warnings
warnings.filterwarnings('ignore')


try:
    os.mkdir("files")
except:
    pass

ssl._create_default_https_context = ssl._create_unverified_context

with urllib.request.urlopen('https://courses.cs.tau.ac.il/pyProg/2526a/resources/notebook_resources.zip') as f:
    content = f.read()

with open('files/notebook_resources.zip', 'wb') as f:
    f.write(content)

with zipfile.ZipFile('files/notebook_resources.zip', 'r') as zip_ref:
    zip_ref.extractall('files')

print(os.listdir('files'))

['baby.png', 'countries-of-the-world.csv', 'dialation.png', 'dialation_2.png', 'dog.png', 'dog_noised.png', 'erosion.png', 'erosion_2.png', 'evil_morty_1.png', 'evil_morty_change.png', 'evil_morty_change_3.png', 'evil_morty_change_noised.png', 'evil_morty_segmentation.png', 'ex1.csv', 'ex2.csv', 'foods.txt', 'infile1.txt', 'infile2.txt', 'koala.png', 'monday.txt', 'notebook_resources.zip', 'orders_2_2024.csv', 'orders_3_2024.csv', 'orders_4_2024.csv', 'out.txt', 'products2.csv', 'ship.png', 'StudentsGrades.csv', 'sunday.txt', 'witcher_1.csv', 'witcher_2.csv', 'woman_noised.png', '__MACOSX']


**שימו לב**: על מנת להריץ את התאים ב-Live Code, יש לייבא תחילה את ספרית `pandas` ע"י הרצת השורת הראשונה בתא למטה.   
בנוסף, נגביל את מספר השורות והעמודות שתופענה בהדפסת הטבלאות ע"י שורות הקוד השניה והשלישית:

In [1]:
import pandas as pd
pd.options.display.max_rows=5
pd.options.display.max_columns=5

בפרק זה נתחיל להכיר את אחת מהיכולות החזקות ביותר של pandas: קיבוץ נתונים לפי קטגוריות או תכונות משותפות, באמצעות המתודה `groupby`. פונקציה זו מאפשרת לנו לבצע חישובים סטטיסטיים, סיכומים וטרנספורמציות שונות עבור תת-קבוצות של הנתונים, מבלי לכתוב לולאות מסובכות. נלמד כיצד לקבץ טבלאות לפי ערך בעמודה, לבצע פעולות כמו סכום, ממוצע ומניין על כל קבוצה.

## `groupby` - סיכום קבוצות של שורות לכדי שורה בודדת

המתודה `groupby` מאפשרת לבצע שאילתות מתקדמות באמצעות חלוקת הנתונים לקבוצות על פי **ערכים בעמודה מסוימת** (או במספר עמודות), ולאחר מכן להפעיל על כל קבוצה חישובים ופעולות סיכום.   

לדוגמא, נניח כי בטבלת ציוני הסטודנטים שלנו קיימת עמודה נוספת בשם `Degree` המייצגת את התואר אותו לומד כל סטודנט. נוכל להשתמש ב־`groupby("Degree")` כדי לאסוף את כל הסטודנטים של כל תואר לקבוצה אחת, ואז לחשב ממוצע ציונים בכל קורס **לכל תואר בנפרד**.  

כדי לממש את התרחיש לעיל, נוסיף לטבלה שלנו עמודה חדשה בשם "Degree"  


In [191]:
inputFileName = "files/StudentsGrades.csv"
df = pd.read_csv(inputFileName)
df['Degree']=["Industrial", "Industrial", "mechanical", \
              "Industrial", "Industrial", "electrical", \
              "electrical", "electrical", "electrical", \
              "bio-medical", "bio-medical", "mechanical", "mechanical"]
display(df)

Name  Programming  Marine Biology  Stellar Cartography  Math  History  \
0    Yael           50              56                   70    60       87   
1   Nadav           61              77                   75    75       63   
..    ...          ...             ...                  ...   ...      ...   
11    Tom           98              76                   98   100       98   
12    Adi           76              87                   34    90       88   

    Planet Survival  Art      Degree  
0                65   91  Industrial  
1                52   88  Industrial  
..              ...  ...         ...  
11               92   80  mechanical  
12               84   70  mechanical  

[13 rows x 9 columns]

## התחביר של `groupby` 

#### <span style='color:green'>()</span>df.<span style='color:red'>groupby(x)</span><span style='color:blue'>[y]</span>.<span style='color:green'>op</span>

- <span style='color:red'>חלוקת ה־`DataFrame` לקבוצות (טבלאות משנה מסוג `DataFrame`) לפי הערכים בעמודה או בעמודות `x`</span>  
- <span style='color:blue'>בחירת העמודה או העמודות עליהן נרצה לבצע את סיכום הערכים - `y`</span>  
- <span style='color:green'>ביצוע פעולת סיכום על הערכים של כל קבוצה בנפרד, באמצעות האופרטור/פונקציה המתאימה (`op`). למשל: `mean`, `max`, `min`, `sum`, `count`, `apply`</span>  

שימו לב ש־`x` ו־`y` יכולים להיות עמודה אחת (מחרוזת בודדת `str`) או מספר עמודות (רשימה של מחרוזות).  


לדוגמא, השורה שלהלן מחזירה את הממוצע בקורס תכנות בפילוח לפי סוג תואר:  

In [192]:
df.groupby(["Degree"])['Programming'].mean()

Degree
Industrial     57.25
bio-medical    85.00
electrical     78.25
mechanical     85.00
Name: Programming, dtype: float64

כלומר במקרה זה:
- `x` היה "Degree".  
- `y` היה "Programming".
- `op` היה `mean`.

ואם נרצה לדעת מהו הציון **המקסימלי** שהתקבל בכל קבוצה?   
פשוט נחליף את פעולת הסיכום ל`max`:

In [193]:
df.groupby(["Degree"])['Programming'].max()

Degree
Industrial      82
bio-medical    100
electrical      95
mechanical      98
Name: Programming, dtype: int64

### תרגול 

כתבו שורת קוד בודדת המחלצת את **שם הסטודנט שקיבל את הציון הכי נמוך** בכל תואר (סה"כ 4 סטודנטים כי ישנם 4 תארים).   
הניחו כי בכל תואר קיים סטודנט אחד כזה בדיוק.      

In [1]:
# Write your code here


```{admonition} **רמז**
:class: dropdown, tip
השתמשו ב`idxmin`.

```


```{admonition} **לחצו כאן כדי לצפות בפתרון**
:class: dropdown, tip
באמצעות `groupby` ו`idxmin` נוכל לחלץ את **שם השורה** של הסטודנט שקיבל את הציון הכי נמוך בכל תואר.
לאחר מכן, באמצעות `loc`, נוכל לקבל את השמות שנמצאים באותן השורות, כדי לקבל את שמות הסטודנטים.

``` python
df.loc[df.groupby(["Degree"])['Programming'].idxmin(), 'Name']
```